In [9]:
import pandas as pd
import numpy as np
import spacy
import itertools
import csv
import re
from spacy.lang.en.stop_words import STOP_WORDS
from spacy.tokenizer import Tokenizer
from spacy.pipeline import EntityRuler
from spacy.attrs import *
from spacy.symbols import *
from mlxtend.preprocessing import TransactionEncoder
from mlxtend.frequent_patterns import apriori , association_rules
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer


# Global Variables
infile = 'Apple tweets disambiguated.csv'
nlp = spacy.load('en_core_web_sm')
patternsfile = "entityruler_patterns.jsonl"
nlp.Defaults.stop_words |= {"My","the","it", "a"}
ruler = EntityRuler(nlp).from_disk(patternsfile)
nlp.add_pipe(ruler, before="ner")
analyser = SentimentIntensityAnalyzer()

# Aspect Categories defined based on aspect terms
MON = "cost"
AUD = "audio"
SOFT = "software"
SEC = "security"
SYS = "system"
CAM = "camera"
SUP = "support"
HAW = "hardware"
GEN = "general"


# Aspect term Dictionary 
ASPECTS = { "money": MON, "price": MON, "fee":MON,"charge":MON,
            "headphones":AUD, "headphone jack":AUD,
            "software":SOFT, "data": SOFT, "space":SOFT, "download":SOFT, "touch":SOFT,  
            "security":SEC, "privacy":SEC, "file":SEC, "storage":SEC,
            "system":SYS, "app": SYS, "tv app":SYS,  "text message":SYS, "streaming service":SYS,
            "message":SYS, "emoji": SYS, "game service":SYS, "subscription":SYS, 
            "upgrade":SYS,"update":SYS, 
            "camera": CAM, "photo": CAM, "picture":CAM, "image":CAM,"video":CAM, 
            "support": SUP, "customer support":SUP, "service": SUP,"warranty": SUP,   
            "hardware":HAW, "keyboard":HAW, "screen": HAW, "charger":HAW, "tv": HAW, 
            "battery": HAW, "battery life": HAW,
            "laptop":HAW, "computer": HAW,
            "design":GEN, "quality":GEN      
          }


# Import tweet file
def import_unprocessed_tweets(infile):
    # Reads file stored in global var 'infile' into dict
    # Only stores text columns 
    # Nested lists are comprised of text,hashtag pairs
    with open(infile, 'r') as lines:
        reader = csv.DictReader(lines)
        all_tweets = []
        for line in reader:
            #a_tweet = []
            #an_id = []
            text = line['text']
            id_str = line['id_str']
            #a_tweet.append(text)
            #an_id.append(id_str)
            all_tweets.append([text, id_str])
        # Returns list of lists containing tweet text
        print("Tweet import complete!")
        return all_tweets
    
    
# Helper function 1: Find noun phrase bigrams and/or trigrams in doc depending on token index
# Assumes there are at least three words in doc 
def noun_phrase_utility(doc, i):
    #Finds noun phrases in retokenized doc
 
    zerone = ""
    twoonezero = "" 
    onezero = ""
    zeronetwo = ""
    doc_lower = [token.lower_ for token in doc]
    if len(doc_lower) >= 3:
        phrases = []
        nps_set = set()
        # First index in list
        if i == 0:
            zerone = "{0} {1}".format(doc_lower[i],doc_lower[i + 1])

            zeronetwo = "{0} {1} {2}".format(doc_lower[i], doc_lower[i +1],
                                              doc_lower[i + 2])
            phrases = [zerone, zeronetwo]

        # Second index in list when doc is longer than three words
        elif i == 1 and len(doc_lower) > 3:
            onezero = "{0} {1}".format(doc_lower[i - 1], doc_lower[i])

            zerone = "{0} {1}".format(doc_lower[i],doc_lower[i + 1])

            zeronetwo = "{0} {1} {2}".format(doc_lower[i], doc_lower[i +1],
                                              doc_lower[i + 2])

            phrases = [onezero, zerone, zeronetwo]

        # Second index in list when doc is three words long
        elif i == 1 and len(doc_lower) == 3:
            onezero = "{0} {1}".format(doc_lower[i - 1], doc_lower[i])

            zerone = "{0} {1}".format(doc_lower[i],doc_lower[i + 1])

            phrases = [onezero, zerone]

        # Last index in list
        elif i == (len(doc_lower) - 1):
            onezero = "{0} {1}".format(doc_lower[i - 1], doc_lower[i])

            twoonezero = "{0} {1} {2}".format(doc_lower[i - 2],
                                              doc_lower[i - 1], doc_lower[i]) 

            phrases = [onezero, twoonezero]

        # Second to last index in list when doc is longer than three words
        elif i == (len(doc_lower) - 2):
            onezero = "{0} {1}".format(doc_lower[i - 1], doc_lower[i])

            zerone = "{0} {1}".format(doc_lower[i],doc_lower[i + 1])

            twoonezero = "{0} {1} {2}".format(doc_lower[i - 2],
                                              doc_lower[i - 1], doc_lower[i]) 

            phrases = [onezero, twoonezero, zerone]

        # Everything else    
        else: 
            zerone = "{0} {1}".format(doc_lower[i],doc_lower[i + 1])

            zeronetwo = "{0} {1} {2}".format(doc_lower[i], doc_lower[i +1],
                                              doc_lower[i + 2])

            onezero = "{0} {1}".format(doc_lower[i - 1], doc_lower[i])

            twoonezero = "{0} {1} {2}".format(doc_lower[i - 2],
                                              doc_lower[i - 1], doc_lower[i]) 

            phrases = [onezero, twoonezero, zerone, zeronetwo]

        return phrases
    else:
        return doc_lower


# Helper function 2: Will retokenize doc to remove stop words, punctuation and spaces
def re_tokenize(doc):
    text_list = []
    for token in doc:
        if token.is_stop != True and token.is_punct != True and token.is_space != True:
            text = token.text
            text_list.append(text)
    new_doc = ' '.join(text_list)
    doc = nlp(new_doc)
    
    return doc



# Helper Function 3: Find unique multiword aspects, return aspect list
def multi_word_aspects(new_doc):
    nps_set = set()
    for token in new_doc:
            if token.pos_ == "NOUN":
                if token.lemma_ in ASPECTS:
                    poss_aspects = noun_phrase_utility(new_doc, token.i)
                    for item in poss_aspects:
                        nps_set.add(item)
  
    nps_list = list(nps_set)
    
    return nps_list


# Helper Function 4: Find unique single word aspects, return aspect list
def single_word_aspects(new_doc):
    aspect_set = set()
    for token in new_doc:
        if token.pos_ == "NOUN":
            if token.lemma_ in ASPECTS:
                aspect_set.add(token.lemma_)
                
    aspect_list = list(aspect_set)
    return aspect_list            


# FUNCTION NOT USED
def contains_word(s, w):
    return f' {w} ' in f' {s} '


# Helper Function 5: Delete words that are found to be duplicated accross single and multiword aspect lists
# Used in merge_aspects
def delete_words(deletelist, mainlist):
    # Uses list of indeces to delete items from main_list
    new_list= [aspect for aspect in mainlist if aspect not in deletelist]
    # Returns list of single aspects not found in multiword aspect list
    return new_list


# Helper Function 6: Merges single and multiword aspect lists after duplicates are removed
# Used in opinion_finder
def merge_aspects(single_aspects, multi_aspects):
    # Convert multi-word aspect list to list of single words 
    by_word_aspects = []
    for asp in multi_aspects:
        words = asp.split(' ')
        by_word_aspects.append(words)
    
    single_words = list(itertools.chain.from_iterable(by_word_aspects))
    
    # Compare single word aspects to single_words, if match found, remove word from single words
    to_delete = []
    for s in single_aspects:
        if s in single_words:
            to_delete.append(s)
            
    clean_s_aspects = delete_words(to_delete, single_aspects)
    
    mergedlist = clean_s_aspects + multi_aspects
    return mergedlist
    

# FUNCTION NOT USED
def find_root_verb(doc):
    
    root_verb = [token for token in doc if (token.dep_ == "ROOT")]
        
    return root_verb

# FUNCTION NOT USED
def find_sentiment_words(doc):
    sentiment_words = []
    sentiment_words.append(([token for token in doc if 
                                     (not token.is_stop and not token.is_punct and 
                                      (token.pos_ == "ADJ" or token.pos_ == "VERB" or token.pos_ =="ADV"))]))
    # Return list of tokens that contain sentiment according to criteria
    return sentiment_words


# Helper function: extraction rules
def rule_1(doc):
    
    rule1 = []
    for token in doc:
        if token.dep_ == "amod" and not token.is_stop:
            #check_spelling(token.text)
            rule1.append((token.head.text, token.text))
    return rule1


# Helper function: extraction rules
def rule_2(doc):
    
    rule2 = []
    for token in doc:
        children = token.children
        A = "999999"
        M = "999999"
        for child in children :
            if(child.dep_ == "nsubj" and not child.is_stop):
                A = child.text
                # check_spelling(child.text)

            if((child.dep_ == "dobj" and child.pos_ == "ADJ")and not child.is_stop):
                M = child.text
                #check_spelling(child.text)

        if(A != "999999" and M != "999999"):
            rule2.append((A, M))
    return rule2


# Helper function: extraction rules
def rule_3(doc):
    
    rule3= []
    for token in doc:

        children = token.children
        A = "999999"
        M = "999999"
        for child in children :
            if(child.dep_ == "nsubj" and not child.is_stop):
                A = child.text
                # check_spelling(child.text)

            if(child.dep_ == "acomp" and not child.is_stop):
                M = child.text
                #check_spelling(child.text)

        if(A != "999999" and M != "999999"):
            rule3.append((A, M))
    return rule3


# Helper function: extraction rules
def rule_4(doc):
    rule4 = []
    for token in doc:
        children = token.children
        A = "999999"
        M = "999999"
        for child in children :
            if(child.dep_ == "nsubjpass" and not child.is_stop):
                A = child.text
                # check_spelling(child.text)

            if(child.dep_ == "advmod" and not child.is_stop):
                M = child.text
                #check_spelling(child.text)

        if(A != "999999" and M != "999999"):
            rule4.append((A, M)) # )

    return rule4


# Helper function: extraction rules
def rule_5(doc):
    rule5 = []
    for token in doc:
        children = token.children
        A = "999999"
        buf_var = "999999"
        for child in children :
            if(child.dep_ == "nsubj" and not child.is_stop):
                A = child.text
                # check_spelling(child.text)

            if(child.dep_ == "cop" and not child.is_stop):
                buf_var = child.text
                #check_spelling(child.text)

        if(A != "999999" and buf_var != "999999"):
            rule5.append((A, token.text))

    return rule5


# Helper Function 7: Finds opinions related to aspect terms in tweet
def opinion_rules(doc):
    one = rule_1(doc)
    two = rule_2(doc)
    three = rule_3(doc)
    four = rule_4(doc)
    five = rule_5(doc)
    
    aspects = []
    aspects = one + one + three +four +five
    #dic = {"review_id" : review_id , "aspect_pairs" : aspects}
    return aspects



# Function will return list containing aspect and opinion associated with it if there is one
def opinion_finder(doc):
    pairs = []
    for sent in doc.sents:
        ops = opinion_rules(sent)
        pairs.append(ops)
    
    op_pair = []
    for pair in pairs:
        for p in pair:
            words = ' '.join(p)
            text = words.split()
            for word in text:
                if word.lower() in ASPECTS:
                    op_pair.append(words)
    return op_pair
    

# Function identifies aspects in doc (according to aspects in dictionary) and retursn sentiment score
def aspect_sentiment(doc):
    new_doc = re_tokenize(doc) # Retokenize doc to remove stopwords, punctuation and blank spaces
    m_aspects = multi_word_aspects(new_doc) # Find multi-word aspects
    
    s_aspects = single_word_aspects(new_doc) # Find single-word aspects
    
    # Merge the two while removing duplicate aspects
    # Only multi-word aspects are kept if match is found between two lists
    final_aspects = merge_aspects(s_aspects, m_aspects)

    compound_score = 0
    scores = []
    tot = 0
    if final_aspects: 
        ops = opinion_finder(doc)
        for opinion in ops:
            compound_score = analyser.polarity_scores(opinion)
            scores.append(compound_score['compound'])

        if len(scores) == 1:
            return [scores[0], final_aspects] #found aspect sentiment and > 0 score
        elif len(scores) > 1:
            for num in scores:
                tot = tot + num
            average  = tot / len(scores)
            return [average, final_aspects] #found aspect sentiment and > 0 score
        elif len(scores) == 0:
            return -3 #did not find aspect sentiment
    else:
        return -3 #no aspects present

    
# Function finds aspects score for tweet based on aspect or sentence as a whole     
def tweet_sentiment(doc):
        
        # Find aspect score for aspects in tweet, if any
        score_ops = aspect_sentiment(doc)
        if score_ops == -3:    
            #No aspects (or aspect sentiment) found, sentiment will default to sentence sentiment
            no_asp_score = analyser.polarity_scores(doc.text)
            noas_score = no_asp_score['compound']
            score_type = "Sentence Sentiment"
            return score_type, noas_score, score_ops
        elif score_ops[0] > 0:
            score_type = "Aspect Sentiment"
            return [score_type, score_ops]
        elif score_ops[0] == 0:
            no_asp_score = analyser.polarity_scores(doc.text)
            noas_score = no_asp_score['compound']
            score_type = "Sentence Sentiment"
            return score_type, noas_score, score_ops
            
 
        
#Returns tweet, with its sentiment score and its entities
#Need to add aspects found on here
def senti_process(tweets):
    with open('new_sentiment.csv', "a") as csv_file:
        for tweet in tweets:
            tweet_id = tweet[1]
            doc = nlp(tweet[0])
            doc_ents = []
            for token in doc: 
                if token.ent_type_ in ("ORG", "PRODUCT", "SERVICE", "SOFTWARE"):
                    ent = token.ent_type_
                    doc_ents.append([token.text, ent])
        
            score = tweet_sentiment(doc)
            writer = csv.writer(csv_file, delimiter=',')
            writer.writerow([tweet_id, doc, score, doc_ents])
            print(tweet_id, doc, score, doc_ents)
    
                

    
    
all_tweets = import_unprocessed_tweets(infile)
senti_process(all_tweets)

#TESTING SENTENCES
#The screen size is horrible. At least the sound quality is okay.
#The camera does such a bad job of taking pictures! But the battery life is good
#The update does not fix the issues with the pictures
#The camera does such a bad job of taking pictures! My Cannon does far better
#doc = nlp("The camera does such a bad job of taking pictures! But the battery life is good")
#score = analyser.polarity_scores("camera bad job")
#print(score)


Tweet import complete!
1.0896051702527058e+18 Ok guys its time for Dimonds available now in my repo        RT  #cydia #theme #ios #jailbreak #anemone #iPhone #iPad #new   ('Sentence Sentiment', 0.296, -3) [['RT', 'ORG'], ['ios', 'SOFTWARE'], ['iPhone', 'PRODUCT'], ['iPad', 'PRODUCT']]
1.0896051995876188e+18 It makes me chuckle when articles claim that the Fitbit versa can compete with the Apple Watch. I've had both and the Versa is like 15  years behind in every aspect.  ('Sentence Sentiment', 0.6369, -3) [['Fitbit', 'ORG'], ['Apple', 'ORG'], ['Versa', 'ORG']]
1.0896052118643999e+18 This was pretty cool! Thank you Apple for having me. And thank you to everyone who came !! Had so much fun, super cool chatting about production and songwriting too! #todayatapple   ('Sentence Sentiment', 0.967, -3) [['Apple', 'ORG']]
1.0896052368121037e+18 Bulletinatomic Potus Davos Wef Energy Yearsofliving Mikebloomberg Huawei Theellenshow Apple #HSS #LRAD Jerrybrowngov Un PGA Dairy: US EU.. Money game sa

1.0896065161964749e+18 Pixel 3xl Whitestone Dome Glass Screen Protector #screenprotector #screen #cracked #Galaxy #iPhone #AppleWatch #Pixel #docomo #amazon  #mobilefun #lazada #Qoo10 #zagg #bodyguardz #belkin     Youtube   ('Sentence Sentiment', 0.0, -3) [['iPhone', 'PRODUCT'], ['AppleWatch', 'PRODUCT']]
1.0896065431908516e+18  Come Home Safe  text free drivers #iphone #App free from Techtionary   via Telecomreseller #auto #accidents #SelfDrivingCars #selfdriving   ('Sentence Sentiment', 0.8591, -3) [['iphone', 'PRODUCT'], ['Techtionary', 'ORG'], ['  ', 'ORG']]
1.0896065468819456e+18 Apple iPad mini Price Tracker, real time prices and sales #ipad #apple #ipadmini   ('Sentence Sentiment', 0.0, -3) [['Apple', 'ORG'], ['iPad', 'PRODUCT'], ['ipad', 'PRODUCT'], ['apple', 'ORG']]
1.0896065470371758e+18 2018 15  2.2GHz #Apple #MacBook Pro Silver refurbished, for $2039 at Apple. $360 off! Free ship, 1 yr warranty   ('Sentence Sentiment', 0.5562, -3) [['Apple', 'ORG'], ['MacBook', 'PRODUCT'], 

1.0896078201552527e+18 I will never forgive Apple for ruining the iPhone calculator app ('Sentence Sentiment', -0.4242, -3) [['Apple', 'ORG'], ['iPhone', 'PRODUCT']]
1.0896078721310188e+18   NEWS JUST IN   Dinosaur Assassin: Evolution Now available to download on Facebook Gameroom, or press  PLAY GAME  on our app page! Find us on #facebook  #dinosaur #dino #jurassic #jurassicpark #jurassicworld #facebook #gameroom #iphone #iphone #fun #family #iphone #android   ('Sentence Sentiment', 0.5307, -3) [['iphone', 'PRODUCT'], ['iphone', 'PRODUCT'], ['iphone', 'PRODUCT'], ['android', 'SOFTWARE']]
1.0896078770886861e+18 so just read the requirements to apply for #SettledStatus My wife does not have an android phone she swears by her #iphone and sorry I'm not changing mobile contracts   handsets and data plans just for a system that won't work #brexitshambles #builttofail so now what happens?   ('Sentence Sentiment', -0.0258, -3) [['SettledStatus', 'ORG'], ['android', 'SOFTWARE'], ['iphone', 'PR

1.0896094215404708e+18 Chappers2013 Apple What a shame  ('Sentence Sentiment', -0.4767, -3) [['Apple', 'ORG']]
1.0896096279128474e+18 Chappers2013 Apple And dose it tell you that you cant update your apps ('Sentence Sentiment', 0.0, -3) [['Apple', 'ORG']]
1.089609693729837e+18 Ask Dr. Renee:  Have You Seen The #Apple Holiday TV Ad? Thanks for asking Dr. Renee   #ipadmini ('Sentence Sentiment', 0.6808, -3) [['Apple', 'ORG']]
1.0896097499754455e+18 Get Massive Retweets for #Free Use QuZOOM Free to join and Use. #Ian1 #irtag #asmsg #apple #Ibooks #kobo #spub #new     ('Sentence Sentiment', 0.6705, -3) [['apple', 'ORG']]
1.089609952069673e+18 Pcstevens1368 Apple I only updated my iPhone 5S because it started freezing      #missitnow ('Sentence Sentiment', -0.1027, -3) [['Apple', 'ORG'], ['iPhone', 'PRODUCT']]
1.0896099540659732e+18 How to access your personal Apple Data   #apple ('Sentence Sentiment', 0.0, -3) [['Apple', 'ORG'], ['apple', 'ORG']]
1.0896099631971615e+18 When my peers and co

1.0896113030004654e+18 #business Y know, Apple sure is a curious fruit.  They take away headphone jacks to force EarPod sales then cry b c phone sales flatten. They wont make a touchscreen laptop or full browser tablet to force dual item buy; but cry as msSurface line gains market shareAF. Go figure.   ('Sentence Sentiment', -0.2023, [0.0, ['laptop browser', 'laptop browser tablet', 'nt touchscreen laptop', 'touchscreen laptop']]) [['Apple', 'ORG']]
1.0896113388910428e+18 Hey Apple, whats going on with your update system? Three security updates, thrice the same issue. On the first true reboot after the upgrade, the upgrade system was still  available . I had to reboot like 10 times with a crash on each startup to get it work. #apple #updates ('Sentence Sentiment', 0.6124, [0.0, ['system available reboot', 'upgrade upgrade system', 'updates thrice issue', 'reboot upgrade', 'security updates', 'going update system', 'work apple updates', 'upgrade system available', 'system security', 'up

...

1.1104057212318966e+18 Otts3000 Shivsoul Apple Read the whole concept of it, its not just the physical card, thats just an addition for places that dont accept Apple Pay ('Sentence Sentiment', -0.2235, -3) [['Apple', 'ORG'], ['Apple', 'ORG']]
1.1104057441789379e+18 This. Video. Is. Gorgeous. This is why I love this medium.  ('Sentence Sentiment', 0.8481, -3) []
1.1104057561074156e+18 Ayeeeee about to go into debt again    ('Sentence Sentiment', -0.3612, -3) []
1.1104057874094735e+18 I hope you will like it. Check this out!    1850 #AppleEvent   ('Sentence Sentiment', 0.69, -3) [['AppleEvent', 'ORG']]
1.1104057876152197e+18 InitiativeQ app just released. Here is my invite link:    This link will stop working once I m out of invites. Let me know after you registered, because I need to verify you on my end. #initiativeq #bitcoin #cryptocurrency  #AppleEvent ('Sentence Sentiment', -0.1531, -3) []
1.110405847744725e+18 Monaeravenn Apple He said that wasnt him      I guess thats Apple Music 

1.1104067287497155e+18 Okay all of apple fans, How do you think about #AppleEvent 2019 ???  ('Sentence Sentiment', 0.3485, -3) [['apple', 'ORG']]
1.1104067529550397e+18 Apple Eros Awesomeness!!!! Wait for more!! Erosnow Apple Ridhimalulla   ('Sentence Sentiment', 0.0, -3) [['Apple', 'ORG'], ['Apple', 'ORG']]
1.1104067535590195e+18 Apple's credit card: Their product isn't differentiated, granted, but their influence on global consumer behaviour is going to be a good thing for #neobanking. They've jumped in the pool, a lot of consumers will now follow suit, they just need to refrain from pissing in the pool ('Sentence Sentiment', 0.1852, -3) [['Apple', 'ORG']]
1.1104067779069542e+18 Seems Apple is a bit late coming into the subscription service game and Spending less than Netflix and not stating what the cost is Fail already I will stick with #Netflix ('Sentence Sentiment', -0.5423, -3) [['Apple', 'ORG'], ['Netflix', 'ORG'], ['Netflix', 'ORG']]
1.1104067789515571e+18 Apple News was 1st t

1.1104072885760778e+18 Thread. So the Apple execs said they want to tell the  greatest stories ever told.  Well, first of all, thats a pretty high standard. And I wouldnt mind a new SVOD service reaching for the stars. But, is this just about showcasing the same Hollywood power players? #AppleTVPlus   ('Sentence Sentiment', 0.7003, [0.0, ['service reaching stars', 'new svod service', 'service reaching', 'svod service']]) [['Apple', 'ORG'], ['SVOD', 'ORG']]
1.1104072930893169e+18 The latest Women in Ecommerce News!   Thanks to We Magazine #stadia #appleevent ('Sentence Sentiment', 0.4926, -3) []
1.1104073078866166e+18 I'm having a hard time understanding how this slide is not incredibly unethical when there is an APR of up to 22  on the card. Encouraging people to go into debt with misleading information is not OK.  #AppleEvent   ('Sentence Sentiment', -0.1807, -3) [['AppleEvent', 'ORG']]
1.1104073337781207e+18 He should know how I come with it!  #AppleEvent #ReleaseTheFullMuellerReport

1.1104081652780564e+18 Apple So how much more $ will your next pretend to be Steve Jobs  vision thingy be? ('Sentence Sentiment', 0.1531, -3) [['Apple', 'ORG']]
1.1104081910352732e+18 Apple Does your your new  Card help build credit? ('Sentence Sentiment', 0.6486, -3) [['Apple', 'ORG']]
1.1104082047756411e+18 Apple: For the first time ever, we present you a religion created by humans.  Audience:   #iGOD ('Sentence Sentiment', 0.25, -3) [['Apple', 'ORG']]
1.1104082103416136e+18 God may my business have this kind of favour. This is proof of the word, this is proof of the Covenants made by the Lord, this is proof of the eternal blessing God promised his people and the generations to stem from them after. The righteous and those he saved from Egypt. ('Sentence Sentiment', 0.9233, -3) [['Covenants', 'ORG']]
1.1104082409347359e+18 Apple Arcade:   100 new and exclusive games   Offline Play for every game   Ad free   Available this fall    #AppleEvent   ('Sentence Sentiment', 0.6908, -3) [['Ap

1.110408708096299e+18 Apple announces Apple TV   with all kinds of celebrity storytellers:  : Exclusive Apple Original shows  : Ad free subscription  : Available in 100  countries  : Coming this fall    #AppleEvent   ['Aspect Sentiment', [0.5106, ['subscription available 100', 'subscription available', 'tv kinds celebrity', 'tv kinds', 'announces apple tv', 'ad free subscription', 'free subscription', 'apple tv']]] [['Apple', 'ORG'], ['Apple', 'ORG'], ['Apple', 'ORG'], ['AppleEvent', 'ORG']]
1.1104087170219213e+18 Here's all the original shows introduced for Apple TV  #AppleEvent     ('Sentence Sentiment', 0.3182, -3) [['Apple', 'ORG'], ['AppleEvent', 'ORG']]
1.1104087351160218e+18 Apple next year...  News  TV  Music  App Store  Camera  Calendar  Mail  Notes  Books  Photos  Calculator  Shortcuts  Podcasts  Settings  Voice Memos  Safari   #AppleEvent ('Sentence Sentiment', 0.0, -3) [['Apple', 'ORG']]
1.1104087448929567e+18 Anyone catch an #AppleArcade release date or price? I looked awa